# VacationPy
---

## Starter Code to Import Libraries and Load the Weather and Coordinates Data

In [13]:
# Dependencies and Setup
import hvplot.pandas
import pandas as pd
import requests

# Import API key
from api_keys import geoapify_key

In [14]:
# Load the CSV file created in Part 1 into a Pandas DataFrame
city_data_df = pd.read_csv("output_data/cities.csv")

# Display sample data
city_data_df.head()

City_ID       City      Lat       Lng  Max Temp  Humidity  Cloudiness  \
0        0   ust-nera  64.5667  143.2000    -31.26        99          97   
1        1    iqaluit  63.7506  -68.5145    -21.15        65          75   
2        2   morogoro  -6.8167   37.6667     24.93        86          54   
3        3  kisangani   0.5167   25.2000     32.57        39           6   
4        4       hola  51.5377   23.1902      3.10        81         100   

   Wind Speed Country        Date  
0        0.84      RU  1707320895  
1        8.23      CA  1707320896  
2        0.83      TZ  1707320897  
3        1.59      CD  1707320898  
4        6.54      PL  1707320899

---

### Step 1: Create a map that displays a point for every city in the `city_data_df` DataFrame. The size of the point should be the humidity in each city.

In [3]:
%%capture --no-display

# Configure the map plot
map_plot = city_data_df.hvplot.scatter(x='Lng', y='Lat', c='Humidity', 
                                       geo=True, datashade=True, 
                                       width=800, height=500)
# Display the map
map_plot



:DynamicMap   []
   :RGB   [Lng,Lat]   (R,G,B,A)

### Step 2: Narrow down the `city_data_df` DataFrame to find your ideal weather condition

In [15]:
# Narrow down cities that fit criteria and drop any results with null values
# Define criteria for ideal weather conditions
ideal_weather_df = city_data_df[
    (city_data_df['Max Temp'] < 27) &  
    (city_data_df['Max Temp'] > 21) &  
    (city_data_df['Wind Speed'] < 4.5) & 
    (city_data_df['Cloudiness'] == 0)    
]

# Drop any rows with null values
ideal_weather_df = ideal_weather_df.dropna()

# Display sample data
ideal_weather_df.head()



City_ID                 City      Lat      Lng  Max Temp  Humidity  \
69        69                yanam  16.7333  82.2167     22.73        87   
215      215            tazacorte  28.6290 -17.9293     21.54        64   
248      248  prachuap khiri khan  12.2167  99.7500     21.70        73   
286      286   acapulco de juarez  16.8634 -99.8901     26.90        74   
287      287   brisas de zicatela  15.8369 -97.0419     26.29        78   

     Cloudiness  Wind Speed Country        Date  
69            0        1.03      IN  1707320968  
215           0        2.06      ES  1707321107  
248           0        1.80      TH  1707321137  
286           0        2.57      MX  1707321182  
287           0        4.12      MX  1707321183

### Step 3: Create a new DataFrame called `hotel_df`.

In [16]:
# Use the Pandas copy function to create DataFrame called hotel_df to store the city, country, coordinates, and humidity
hotel_df = city_data_df[['City', 'Country', 'Lat', 'Lng', 'Humidity']].copy()

# Add an empty column, "Hotel Name," to the DataFrame
hotel_df['Hotel Name'] = ''

# Display sample data
hotel_df.head()

City Country      Lat       Lng  Humidity Hotel Name
0   ust-nera      RU  64.5667  143.2000        99           
1    iqaluit      CA  63.7506  -68.5145        65           
2   morogoro      TZ  -6.8167   37.6667        86           
3  kisangani      CD   0.5167   25.2000        39           
4       hola      PL  51.5377   23.1902        81

### Step 4: For each city, use the Geoapify API to find the first hotel located within 10,000 metres of your coordinates.

In [17]:
# Set parameters to search for a hotel
radius = 10000  # Set the radius for the hotel search
params = {
    "categories": "accommodation.hotel", 
    "apiKey" : geoapify_key,
    "limit" : 20  
}

# Print a message to follow up the hotel search
print("Starting hotel search")

# Iterate through the hotel_df DataFrame
for index, row in hotel_df.iterrows():
    # get latitude, longitude from the DataFrame
    lat = row['Lat']
    lng = row['Lng']
    
    # Add filter and bias parameters with the current city's latitude and longitude to the params dictionary
    params["filter"] = f"circle:{lng},{lat},{radius}"
    params["bias"] = f"proximity:{lng},{lat}"
    
    # Set base URL
    base_url = "https://api.geoapify.com/v2/places"

    # Make an API request using the params dictionary
    response = requests.get(base_url, params=params)
    response = response.json()
    # Convert the API response to JSON format
    try:
        hotel_df.loc[index, "Hotel Name"] = response["features"][0]["properties"]["name"]
         
    except (KeyError, IndexError):
        # If no hotel is found, set the hotel name as "No hotel found".
        #hotel_name = "No hotel found"
        
        # Grab the first hotel from the results and store the name in the hotel_df DataFrame
        hotel_df.loc[index, "Hotel Name"] = "No hotel found"
    
    # Log the search results
    print(f"{hotel_df.loc[index, 'City']} - nearest hotel: {hotel_df.loc[index, 'Hotel Name']}")
    
# Display sample data
hotel_df



Starting hotel search
ust-nera - nearest hotel: гостиница "Солнечная"
iqaluit - nearest hotel: Frobisher Inn
morogoro - nearest hotel: B One Lodge
kisangani - nearest hotel: Hotel Kisangani
hola - nearest hotel: No hotel found
new norfolk - nearest hotel: Woodbridge on the Derwent
great falls - nearest hotel: Hotel Arvon
olonkinbyen - nearest hotel: No hotel found
blackmans bay - nearest hotel: Villa Howden
grytviken - nearest hotel: No hotel found
adamstown - nearest hotel: No hotel found
crane - nearest hotel: No hotel found
waitangi - nearest hotel: Hotel Chathams
bredasdorp - nearest hotel: Victoria Hotel
worland - nearest hotel: Town House Motor Inn
enewetak - nearest hotel: No hotel found
whakatane - nearest hotel: Whakatane Hotel
port-aux-francais - nearest hotel: Keravel
kampong cham - nearest hotel: Phnom Pros Hotel
trairi - nearest hotel: Pousada Villa Aurora
papatowai - nearest hotel: No hotel found
sao tome - nearest hotel: Hotel Baia
ushuaia - nearest hotel: Apart Hotel Ai

SSLError: HTTPSConnectionPool(host='api.geoapify.com', port=443): Max retries exceeded with url: /v2/places?categories=accommodation.hotel&apiKey=78932c84d0a642a3b4416657ea2866ca&limit=20&filter=circle%3A145.701%2C15.1355%2C10000&bias=proximity%3A145.701%2C15.1355 (Caused by SSLError(SSLEOFError(8, '[SSL: UNEXPECTED_EOF_WHILE_READING] EOF occurred in violation of protocol (_ssl.c:1007)')))

### Step 5: Add the hotel name and the country as additional information in the hover message for each city in the map.

In [7]:
%%capture --no-display

# Configure the map plot
# YOUR CODE HERE

# Display the map
# YOUR CODE HERE

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Humidity,Hotel Name,Country)